<a href="https://colab.research.google.com/github/GuilhermeRLDev/DeepLearningExperiments/blob/main/audio_exploration.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#Import relevant libraries to build model
!pip install pretty_midi
!pip install wget
!pip install jams

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 85.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.1/51.1 KB 7.5 MB/s eta 0:00:00
  Created wheel for pretty_midi: filename=pretty_midi-0.2.9-py3-none-any.whl size=5591954 sha256=c4b4522e4375cb0a0907ab013d81c8c275391100e6d5edeacd3127530fd43b80
  Stored in directory: /root/.cache/pip/wheels/2a/5a/e3/30eeb9a99350f3f7e21258fcb132743eef1a4f49b3505e76b6
Successfully built pretty_midi
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
  Created wheel for wget: filename=wget-3.2-py3-none-any.whl size=9674 sha256=6aa49dc6832e5126db1257091a2d6e2a660ff9426f67128cb2add01efc5ab12a
  Stored in directory: /root/.cache/pip/wheels/bd/a8/c3/3cf2c14a1837a4e04bd98631724e81f33f462d86a1d895fae0
Successfull

In [ ]:
import os
import wget
from google.colab import drive
drive.mount("/content/gdrive")

Mounted at /content/gdrive


In [ ]:
os.listdir("gdrive/MyDrive/datasets")

['data', '.ipynb_checkpoints', 'labels']

In [ ]:
!mkdir /gdrive/MyDrive/datasets/data

mkdir: cannot create directory ‘/gdrive/MyDrive/datasets/data’: No such file or directory


In [ ]:
!unzip gdrive/MyDrive/datasets/audio_hex-pickup_original.zip -d gdrive/MyDrive/datasets/data

unzip:  cannot find or open gdrive/MyDrive/datasets/audio_hex-pickup_original.zip, gdrive/MyDrive/datasets/audio_hex-pickup_original.zip.zip or gdrive/MyDrive/datasets/audio_hex-pickup_original.zip.ZIP.


In [ ]:
!unzip gdrive/MyDrive/datasets/annotation.zip -d gdrive/MyDrive/datasets/labels

unzip:  cannot find or open gdrive/MyDrive/datasets/annotation.zip, gdrive/MyDrive/datasets/annotation.zip.zip or gdrive/MyDrive/datasets/annotation.zip.ZIP.


In [ ]:
from IPython.core.magics.code import find_source_lines
import jams
import librosa as lr
import IPython.display

In [ ]:
#Constants 
guitarset_path = "gdrive/MyDrive/datasets"

#Loading and preprocessing functions
def get_dataset(path, total_samples):
  '''
    Return x number of samples from disk 
  '''
  data_path = f"{path}/data"
  labels_path = f"{path}/labels"
  data = os.listdir(data_path)
  labels = os.listdir(labels_path)

  files = {}
  i = 0
  for file in labels:

    if i == total_samples:
      break

    file_name = file.split(".")[0]
    if file_name in files:
      continue
    
    # Load data and anotation for the samples
    files[file_name] = {}
    files[file_name]["data"] = lr.load(f"{data_path}/{file_name}_hex.wav")
    files[file_name]["label"] = jams.load(f"{labels_path}/{file_name}.jams")
    i += 1

  return files


In [ ]:
dataset = get_dataset(guitarset_path, 2)

In [ ]:
import IPython

music =  list(dataset.keys())
for m in music: 
  value  = dataset[m]["data"][0]
  print(value)
  sr = dataset[m]["data"][1] 
  print(sr)
  IPython.display.display(IPython.display.Audio(value, rate=sr))

[8.44167825e-03 1.34285036e-02 1.28333485e-02 ... 4.57120696e-05
 1.22576079e-04 1.13071437e-04]
22050


[ 2.0055333e-02  2.8161624e-02  2.2369893e-02 ... -7.5891279e-05
 -1.2151437e-04  0.0000000e+00]
22050


In [ ]:
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
#IPython.display.display(IPython.display.Audio(value, rate=sr)) 

In [25]:
SAMPLE_RATE = 16000
HOP_SIZE = 128

signal = dataset[music[0]]["data"][0]
frame_lenght = lr.time_to_frames(10)

if sr != SAMPLE_RATE:
  signal = lr.resample(signal, sr, SAMPLE_RATE)

frames_per_second = SAMPLE_RATE / HOP_SIZE

spec = lr.stft(signal)

signal = np.pad(signal, [0, HOP_SIZE - len(signal) % HOP_SIZE], mode='constant')
frames = tf.signal.frame(signal, frame_length=HOP_SIZE,frame_step=HOP_SIZE, pad_end=True)

times = np.arange(len(frames))/ frames_per_second

IPython.display.display(IPython.display.Audio(signal, rate = SAMPLE_RATE))

print(times[0], times[1], times[2])


0.0 0.008 0.016


In [23]:
#print(frames[125])

print(times)

[ 1.84118458  3.98816871  2.0348127   4.1587356   4.48447256  4.65549297
 20.50195556 21.62157007 21.87157007 21.96871293 22.16819138 23.237239
 24.32581043 24.8819102  27.7917288  28.1395746  28.32596916  0.22642268
  2.35245442  4.71392834  6.18488073  6.28059501  6.39517551  6.54458594
  8.44501678  8.57338413  8.89347483 10.46547029 10.71971066 11.07674014
 12.64420045 12.77764717 12.93138866 13.03506213 13.56753379 14.15533424
 14.72973333 16.94562902 18.854722   19.01651338 19.42737506 20.01215964
 20.17825941 22.39066304 22.49726168 22.66408707 22.79535692 22.88599184
 25.43562902 25.99460862 27.05687619 27.15621859 27.26136599 28.66857687
 28.87900771 30.27084444 30.54925714 30.82900771 30.95299864 31.38551565
 15.05111655 16.20347483 16.56587846 16.81152472 17.21079909 17.69336145
 18.30998277 18.46011882 18.55728435 29.22612789 29.54821406 29.77828209
 29.93567438 31.7064     32.06782857 32.21215964 32.57238639 32.82612789]


In [14]:
import pretty_midi
import numpy as np

#Rewrite this function to convert jams to Midi
def jams_to_midi(jam, q=1):
    #Create 
    midi = pretty_midi.PrettyMIDI()
    annotations = jam.search(namespace='note_midi')
    if len(annotations) == 0:
        annotations = jam.search(namespace='pitch_midi')
    for anno in annotations:
        midi_ch = pretty_midi.Instrument(program=25)
        for note in anno:
            pitch = int(round(note.value))
            bend_amount = int(round((note.value - pitch) * 4096))
            st = note.time
            dur = note.duration
            n = pretty_midi.Note(
                velocity=100 + np.random.choice(range(-5, 5)),
                pitch=pitch, start=st,
                end=st + dur
            )
            pb = pretty_midi.PitchBend(pitch=bend_amount * q, time=st)
            midi_ch.notes.append(n)
            midi_ch.pitch_bends.append(pb)
        if len(midi_ch.notes) != 0:
            midi.instruments.append(midi_ch)
    return midi

def midi2list(midi):
  midi_list = []

  for instrument in midi.instruments:
    for note in instrument.notes:
      midi_list.append([note.start, note.end, note.pitch, note.velocity])

  return np.array(midi_list)
  
for m in music: 
  values  = jams_to_midi(dataset[m]['label'])
  m_list = midi2list(values)
  print(len(m_list))
  #IPython.display.display(IPython.display.Audio(values.synthesize(fs=22050), rate=22050))

times = m_list[:,0]
index = np.argsort(times)

m_list = m_list[index]

print(m_list)
#print(jams_to_midi)

368
78
[[  0.22642268   1.7995746   61.          95.        ]
 [  1.84118458   1.97469932  53.          95.        ]
 [  2.0348127    2.20896236  58.          99.        ]
 [  2.35245442   3.90819138  60.          99.        ]
 [  3.98816871   4.15070839  53.         100.        ]
 [  4.1587356    4.33288526  55.         103.        ]
 [  4.48447256   4.65281723  58.          99.        ]
 [  4.65549297   4.86447256  50.         101.        ]
 [  4.71392834   6.14195556  60.          95.        ]
 [  6.18488073   6.27776054  60.          99.        ]
 [  6.28059501   6.37347483  61.         104.        ]
 [  6.39517551   6.54030023  60.         104.        ]
 [  6.54458594   6.6142458   59.          96.        ]
 [  8.44501678   8.5378966   58.         102.        ]
 [  8.57338413   8.75914376  58.         103.        ]
 [  8.89347483  10.24603719  58.          98.        ]
 [ 10.46547029  10.69766984  59.          99.        ]
 [ 10.71971066  10.93449524  58.         102.        ]
 [ 

In [26]:
class Vocaburary:
  #Build a vocabulary based on the MT3 paper proposal
  def __init__(self, note_range=128, instrument=128, time=250):
    self.note_range = note_range
    self.instrument = instrument
    self.time = time 
    #Find a way to encode time properly


In [58]:
import fastdtw
from sklearn.neighbors import KNeighborsClassifier

def vocabulary_definition():
  #dictionary of all possible combinations of words 
  pass

def align_frames_to_midi(frames, midi_rep, shift):
  '''
    Align frames to MIDI to help and build a vocabulary
  '''
  start_time_frames = np.array([])

  curr_time = 0
  for index in range(len(frames)): 
    start_time_frames = np.append(start_time_frames, curr_time)
    curr_time += shift

  midi_start_time =  midi_rep[:,0]

  #Apply fastdwt for sequence
  total_mismatch, mapping = fastdtw.fastdtw(start_time_frames, midi_start_time)

  #Get MIDI Labels for dataset
  midi_labels = np.array([midi_rep[j] for i, j in mapping])

  return total_mismatch, midi_labels

def compress_representation(midi_rep_expanded):
    #Identify changes in the variation of samples and collapse repeating events
    collapsed_midi_rep = []

    curr_note = None
    for item in midi_rep_expanded:
      
      #Initialize current note and items
      if curr_note is None:
        curr_note = item
        collapsed_midi_rep.append(curr_note)

      #Start to merge duplicate events
      if (curr_note[0] != item[0]) or (curr_note[2] != item[2]):
        collapsed_midi_rep.append(curr_note)
        curr_note = item

    return collapsed_midi_rep

def to_pretty_midi(collapsed_representation):

  #Focused on guitar generates pretty Midi instrument  
  midi =  pretty_midi.PrettyMIDI()
  instrument = pretty_midi.Instrument(program=25)

  #Map notes to the instrument 
  for n in collapsed_representation:
    instrument.notes.append(pretty_midi.Note(velocity=n[3], pitch= n[2], start=n[0], end=n[1]))

  midi.instruments.append(instrument)

  return midi 

def to_vacab(frames, midi_annotations, times):
  def get_event(e):
    events = {1: 'shift', 2: 'note', 3: 'on', 4:'off', 5: 'time' }

    return events[e]

  indexes = np.arange(len(frames))

  #cost, aligned = align_frames_to_midi(frames, midi_annotations, frames[1])

  events = np.arange(len(frames))
  events_start_index = np.array([])
  events_end_index = np.array([])

  #Implements a KNN classifier to predict start and end for notes within the sequence
  start_time_predictor = KNeighborsClassifier()
  x_times = times.reshape(-1, 1)
  print(times)
  start_time_predictor.fit(x_times, indexes)

  #Use the KNN classifier to implement the algorithm
  m_note_start = midi_annotations[:,0]
  m_times = m_note_start.reshape(-1, 1)
  event_indexes = start_time_predictor.predict(m_times)

  #Implements a KNN classifier to predict start and end for notes within the sequence
  end_time_predictor = KNeighborsClassifier()
  x_times = times.reshape(-1, 1)
  end_time_predictor.fit(x_times, indexes)

  #Use the KNN classifier to implement the algorithm
  m_note_start = midi_annotations[:,1]
  m_times = m_note_start.reshape(-1, 1)
  end_event_indexes = end_time_predictor.predict(m_times) 

  events = dict.fromkeys(indexes)

  for i in range(len(events)):
    events[i] = []
    events[i].append('shift')

  #feed notes on events
  i = 0 
  for index in event_indexes:
    events[index].append(get_event(3))
    events[index].append(f"{get_event(2)}{int(midi_annotations[i, 2])}")
    i += 1
  
  i = 0 
  for index in end_event_indexes:
    events[index] = []
    events[index].append(get_event(4))
    events[index].append(f"{get_event(2)}{int(midi_annotations[i, 2])}")
    i +=1

  print(list(events.values()))
  print(event_indexes)
  print(end_event_indexes)
  print(f"start: {times[event_indexes[0]]} - end time: {times[end_event_indexes[0]]}")

  return list(events.values())

  #Get the nearest neighbour to build an event start
  #print(len(frames))

def from_vocab_to_midi(vocab):
  def get_note(note):
    return int(note[-2:])

  #Every shift event will increment the time for the open notes by one 
  def increment_time_for_open_notes(open_notes, frame_time):
    #Increment each open note by the time
    for note in list(open_notes.keys()): 
      open_notes[note]['duration'] += frame_time

    return open_notes

  #Add or remove open notes according to the state
  def handle_open_note(state, note, time, open_notes, midi_rep):
    print("here")
    print(state)
    print(note)
    if state == 'on':
      print("here")
      if not note in open_notes:
        open_notes[note] = {}
        open_notes[note]['duration'] = 0
        open_notes[note]['start'] = time 
    elif state == 'off':
      if note in open_notes:
        start = open_notes[note]['start']
        end = start + open_notes[note]['duration'] 
        midi_rep.append([start, end, get_note(note), 100])
        del open_notes[note]
      
    return open_notes, midi_rep

  #Implement logic to close open notes upon ties
  #Note that this imeplementation must be created as part of the function

  #Open notes - get all open notes and add to the model
  midi_notes = []
  open_notes = {} 

  time = 0
  for frame in vocab:
    if (len(frame) > 1):
      print(frame)

    state = None
    for event in frame:
      if event == 'shift':
        open_notes = increment_time_for_open_notes(open_notes, 0.008) #TODO Remove hardcoded time for the frame 
      elif event == 'on' or event == 'off':
        state = event 
      elif event[0:4] == ('note'):
        open_notes, midi_notes = handle_open_note(state, event, time, open_notes, midi_notes)
        state = None

    time += 0.008

  #Closes any open notes that have not been closed yet
  for event in list(open_notes.keys()):
    open_notes, midi_notes = handle_open_note('off', event, time, open_notes, midi_notes) 

  return midi_notes

vocab = to_vacab(frames, m_list, times)
back_to_midi = from_vocab_to_midi(vocab)
print(back_to_midi)

midi_rep = to_pretty_midi(back_to_midi)
audio = midi_rep.synthesize()
IPython.display.display(IPython.display.Audio(audio, rate=44100))

#cost, aligned = align_frames_to_midi(frames, m_list, 0.10)
#print(aligned)

#compressed = compress_representation(aligned)
#print(len(compressed))

#midi_rep = to_pretty_midi(compressed)
#audio = midi_rep.synthesize()
#IPython.display.display(IPython.display.Audio(audio, rate=44100))


[0.0000e+00 8.0000e-03 1.6000e-02 ... 2.8784e+01 2.8792e+01 2.8800e+01]
[['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift', 'on', 'note61'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift'], ['shift']

In [52]:
a = '16565546'
print(a[-3:])

546


In [ ]:
indexes = np.arange(100)
print(indexes)

[ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23
 24 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 45 46 47
 48 49 50 51 52 53 54 55 56 57 58 59 60 61 62 63 64 65 66 67 68 69 70 71
 72 73 74 75 76 77 78 79 80 81 82 83 84 85 86 87 88 89 90 91 92 93 94 95
 96 97 98 99]


In [ ]:
annotations = dataset[music[0]]['label'].search(namespace="note_midi")

for annotation in annotations:
  for note in annotation:
    print(note)

Observation(time=9.28770702947844, duration=0.22639455782314144, value=39.9584944748712, confidence=None)
Observation(time=9.628115192743735, duration=0.2612244897959215, value=41.99846030181263, confidence=None)
Observation(time=9.889815873015891, duration=0.272834467120191, value=41.97027104899995, confidence=None)
Observation(time=10.167933786848067, duration=0.6211337868480769, value=42.03844503765588, confidence=None)
Observation(time=10.804600453514752, duration=0.5979138321995379, value=42.012269942338165, confidence=None)
Observation(time=11.407797732426303, duration=0.26702947845805625, value=42.044899278368035, confidence=None)
Observation(time=11.67804716553286, duration=0.3134693877551058, value=42.0533303717264, confidence=None)
Observation(time=11.994419047619033, duration=0.5804988662131336, value=42.00450500486585, confidence=None)
Observation(time=12.605779591836722, duration=0.6037188208616726, value=42.00041155464082, confidence=None)
Observation(time=13.213443990929

In [ ]:
!ls /gdrive/MyDrive/guitarSet/data/

00_BN1-129-Eb_comp_hex.wav    03_BN1-129-Eb_comp_hex.wav
00_BN1-129-Eb_solo_hex.wav    03_BN1-129-Eb_solo_hex.wav
00_BN1-147-Gb_comp_hex.wav    03_BN1-147-Gb_comp_hex.wav
00_BN1-147-Gb_solo_hex.wav    03_BN1-147-Gb_solo_hex.wav
00_BN2-131-B_comp_hex.wav     03_BN2-131-B_comp_hex.wav
00_BN2-131-B_solo_hex.wav     03_BN2-131-B_solo_hex.wav
00_BN2-166-Ab_comp_hex.wav    03_BN2-166-Ab_comp_hex.wav
00_BN2-166-Ab_solo_hex.wav    03_BN2-166-Ab_solo_hex.wav
00_BN3-119-G_comp_hex.wav     03_BN3-119-G_comp_hex.wav
00_BN3-119-G_solo_hex.wav     03_BN3-119-G_solo_hex.wav
00_BN3-154-E_comp_hex.wav     03_BN3-154-E_comp_hex.wav
00_BN3-154-E_solo_hex.wav     03_BN3-154-E_solo_hex.wav
00_Funk1-114-Ab_comp_hex.wav  03_Funk1-114-Ab_comp_hex.wav
00_Funk1-114-Ab_solo_hex.wav  03_Funk1-114-Ab_solo_hex.wav
00_Funk1-97-C_comp_hex.wav    03_Funk1-97-C_comp_hex.wav
00_Funk1-97-C_solo_hex.wav    03_Funk1-97-C_solo_hex.wav
00_Funk2-108-Eb_comp_hex.wav  03_Funk2-108-Eb_comp_hex.wav
00_Funk2-108-Eb_solo_hex.wav  0